# Part 2
In the first part, we have seen how to compute joint probability of a sentence using the independence assumption.
However, this assumption is too weak as words do depend on each other. In the second part, we would like to introduce a better approach using Markov chain.

# Markov chain

Markov chain is based on the following assumption: *given the present, the future does not depend on the past*.

##### Zeroth order Markov chain
The simplest form of Markov chain is so called zeroth order Markov chain where words are completely independent from each other:

$p(w_1\ w_2\ \dots\ w_{|T|}) \approx p(w_1)\ p(w_2)\ p(w_3)\ \dots \ p(w_{|T|}) = \prod^{|T|}_{i=1}p(w_i)$

Recall that this is similar to the independence assumption covered in the first part.
In literature, this probabilistic model is also known as unigram language model.

##### First order Markov chain:
In the first order Markov chain, a probability of a word is conditioned only on the preceeding word:

$p(w_1\ w_2\ \dots\ w_{|T|}) \approx p(w_1)\ p(w_2|w_1)\ p(w_2|w_3)\ \dots \ p(w_{|T|}|w_{|T|-1}) = p(w_1)\prod^{|T|}_{i=2}p(w_i|w_{i-1})$

where conditional probabilities are estimated as:

$p(w_i|w_{i-1})=\frac{count(w_{i-1}\ w_{i})}{count(w_{i-1})}$

In literature, this probabilistic model is called bigram (or 2-gram) language model.

Similarly, in the N-th order Markov chain, a probability of a word is conditioned only on the preceeding N words.


For each of the following tasks we will continue working with PTB dataset.

### Task 1: Computing probability of a sentence (first order Markov chain)
Write a function called **compute_prob1** which takes a sentence as input (and maybe some additional arguments) and returns its probability estimated using the first order Markov chain. 

Your function should first append **\<bos>** and **\<eos>** symbols to the input sentence  and replace all words that are not present in the dictionary with **\<unk>** symbol. 

If the original sentence was "my name is madina", then "madina" is obviously not in the dictionary (see the description of the PTB). The probability of such sentence can be computed as:
  p("my name is madina") = p("my" | "\<bos>") * p("name" | "my") * p("is" | "name") * p("\<unk>" | "is") * p("\<eos>" | "\<unk>")
  

In [1]:
with open('ptb.train.txt') as f:
   raw_data = f.read()  

In [2]:
data = raw_data.split('\n')
data = [sent for sent in data if sent != '']

In [3]:
stop = ('...', '.', '?', '!', '!!!')
data2 = data
data2 = ['<bos>'+sent+'<eos>' for sent in data2]

In [4]:
dictionary = dict()
for i in range(len(data2)):
    words = data2[i].split()
    for word in words:
        dictionary[word] = dictionary.get(word, 0) + 1
print(dictionary)

{'<bos>': 42068, 'aer': 1, 'banknote': 1, 'berlitz': 1, 'calloway': 1, 'centrust': 1, 'cluett': 1, 'fromstein': 1, 'gitano': 1, 'guterman': 1, 'hydro-quebec': 1, 'ipo': 1, 'kia': 1, 'memotec': 1, 'mlx': 1, 'nahb': 1, 'punts': 1, 'rake': 1, 'regatta': 1, 'rubens': 1, 'sim': 1, 'snack-food': 1, 'ssangyong': 1, 'swapo': 1, 'wachter': 1, '<eos>': 42068, 'pierre': 6, '<unk>': 45020, 'N': 32481, 'years': 1241, 'old': 268, 'will': 3270, 'join': 45, 'the': 50770, 'board': 612, 'as': 4833, 'a': 21196, 'nonexecutive': 6, 'director': 359, 'nov.': 259, 'mr.': 4326, 'is': 7337, 'chairman': 635, 'of': 24400, 'n.v.': 13, 'dutch': 28, 'publishing': 64, 'group': 928, 'rudolph': 8, 'and': 17474, 'former': 306, 'consolidated': 37, 'gold': 165, 'fields': 44, 'plc': 114, 'was': 4073, 'named': 210, 'this': 2438, 'british': 337, 'industrial': 243, 'conglomerate': 22, 'form': 115, 'asbestos': 27, 'once': 219, 'used': 372, 'to': 23638, 'make': 646, 'kent': 11, 'cigarette': 18, 'filters': 11, 'has': 3494, 'caus

In [5]:
dictionary2 = dict()
for i in range(len(data2)):
    words = data2[i].split()
    print(words)
    #for word in words:
        #print(word)
        #if word[i], word[i-1] in dictionary:
        #   dictionary2[word[i], word[i-1]]+=1
        #else:
        #    dictionary2[word[i], word[i-1]]=1
print(dictionary)

['<bos>', 'aer', 'banknote', 'berlitz', 'calloway', 'centrust', 'cluett', 'fromstein', 'gitano', 'guterman', 'hydro-quebec', 'ipo', 'kia', 'memotec', 'mlx', 'nahb', 'punts', 'rake', 'regatta', 'rubens', 'sim', 'snack-food', 'ssangyong', 'swapo', 'wachter', '<eos>']
['<bos>', 'pierre', '<unk>', 'N', 'years', 'old', 'will', 'join', 'the', 'board', 'as', 'a', 'nonexecutive', 'director', 'nov.', 'N', '<eos>']
['<bos>', 'mr.', '<unk>', 'is', 'chairman', 'of', '<unk>', 'n.v.', 'the', 'dutch', 'publishing', 'group', '<eos>']
['<bos>', 'rudolph', '<unk>', 'N', 'years', 'old', 'and', 'former', 'chairman', 'of', 'consolidated', 'gold', 'fields', 'plc', 'was', 'named', 'a', 'nonexecutive', 'director', 'of', 'this', 'british', 'industrial', 'conglomerate', '<eos>']
['<bos>', 'a', 'form', 'of', 'asbestos', 'once', 'used', 'to', 'make', 'kent', 'cigarette', 'filters', 'has', 'caused', 'a', 'high', 'percentage', 'of', 'cancer', 'deaths', 'among', 'a', 'group', 'of', 'workers', 'exposed', 'to', 'it', 

['<bos>', 'a', 'spokesman', 'for', 'the', 'guild', 'said', 'the', 'union', "'s", 'lawyers', 'are', 'reviewing', 'the', 'suit', '<eos>']
['<bos>', 'he', 'said', 'disciplinary', 'proceedings', 'are', 'confidential', 'and', 'declined', 'to', 'comment', 'on', 'whether', 'any', 'are', 'being', 'held', 'against', 'mr.', 'trudeau', '<eos>']
['<bos>', 'mr.', 'trudeau', "'s", 'attorney', 'norman', 'k.', '<unk>', 'said', 'the', '<unk>', 'consists', 'mainly', 'of', 'the', 'guild', "'s", '<unk>', 'threats', 'of', 'disciplinary', 'action', '<eos>']
['<bos>', 'mr.', '<unk>', 'said', 'a', 'guild', 'disciplinary', 'hearing', 'is', 'scheduled', 'next', 'monday', 'in', 'new', 'york', '<eos>']
['<bos>', 'mr.', '<unk>', 'who', 'will', 'go', 'before', 'the', 'disciplinary', 'panel', 'said', 'the', 'proceedings', 'are', 'unfair', 'and', 'that', 'any', 'punishment', 'from', 'the', 'guild', 'would', 'be', '<unk>', '<eos>']
['<bos>', 'in', 'addition', 'to', 'the', 'damages', 'the', 'suit', 'seeks', 'a', 'court

['<bos>', 'the', 'action', 'on', 'poland', 'came', 'as', 'the', 'conference', 'separately', 'approved', '$', 'N', 'million', 'for', 'international', 'population', 'planning', 'activities', 'an', 'N', 'N', 'increase', 'over', 'fiscal', 'N', '<eos>']
['<bos>', 'the', 'house', 'and', 'senate', 'are', 'divided', 'over', 'whether', 'the', 'united', 'nations', 'population', 'fund', 'will', 'receive', 'any', 'portion', 'of', 'these', 'appropriations', 'but', 'the', 'size', 'of', 'the', 'increase', 'is', 'itself', 'significant', '<eos>']
['<bos>', 'in', 'a', 'second', 'area', 'of', 'common', 'concern', 'the', 'world', 'environment', 'an', 'additional', '$', 'N', 'million', 'will', 'be', 'provided', 'in', 'development', 'assistance', 'to', 'fund', 'a', 'series', 'of', 'initiatives', 'related', 'both', 'to', 'global', 'warming', 'and', 'the', 'plight', 'of', 'the', 'african', 'elephant', '<eos>']
['<bos>', 'the', 'sweeping', 'nature', 'of', 'the', 'bill', 'draws', 'a', 'variety', 'of', 'special'

['<bos>', 'n.v', '<unk>', 'said', 'net', 'income', 'in', 'the', 'third', 'quarter', 'jumped', 'N', 'N', 'as', 'the', 'company', 'had', 'substantially', 'lower', 'extraordinary', 'charges', 'to', 'account', 'for', 'a', 'restructuring', 'program', '<eos>']
['<bos>', 'the', 'dutch', 'chemical', 'group', 'said', 'net', 'income', 'gained', 'to', 'N', 'million', 'guilders', '$', 'N', 'million', 'or', 'N', 'guilders', 'a', 'share', 'from', 'N', 'million', 'guilders', 'or', 'N', 'guilders', 'a', 'share', 'a', 'year', 'ago', '<eos>']
['<bos>', 'the', 'N', 'N', 'state-owned', '<unk>', 'had', 'eight', 'million', 'guilders', 'of', 'extraordinary', 'charges', 'in', 'the', 'latest', 'quarter', 'mainly', 'to', 'reflect', 'one-time', 'losses', 'in', 'connection', 'with', 'the', 'disposal', 'of', 'some', 'operations', '<eos>']
['<bos>', 'the', 'charges', 'were', 'offset', 'in', 'part', 'by', 'a', 'gain', 'from', 'the', 'sale', 'of', 'the', 'company', "'s", 'construction', 'division', '<eos>']
['<bos>',

['<bos>', 'today', 'the', '<unk>', '<unk>', 'has', 'mostly', 'dropped', 'the', '<unk>', 'work', 'though', 'a', 'touch', 'of', 'the', 'old', '<unk>', 'still', '<unk>', 'and', 'now', 'goes', 'on', 'the', 'road', 'with', 'piano', 'bass', 'a', 'slide', 'show', 'and', 'a', '<unk>', 'that', 'ranges', 'from', 'light', 'classical', 'to', 'light', 'jazz', 'to', 'light', 'pop', 'with', 'a', 'few', 'notable', 'exceptions', '<eos>']
['<bos>', 'just', 'the', 'thing', 'for', 'the', '<unk>', 'set', 'the', '<unk>', 'audience', 'that', 'has', 'embraced', 'new', 'age', 'as', 'its', 'very', 'own', 'easy', 'listening', '<eos>']
['<bos>', 'but', 'you', 'ca', "n't", 'dismiss', 'mr.', 'stoltzman', "'s", 'music', 'or', 'his', '<unk>', 'as', 'merely', 'commercial', 'and', '<unk>', '<eos>']
['<bos>', 'he', 'believes', 'in', 'what', 'he', 'plays', 'and', 'he', 'plays', '<unk>', '<eos>']
['<bos>', 'his', 'recent', 'appearance', 'at', 'the', 'metropolitan', 'museum', 'dubbed', 'a', 'musical', '<unk>', 'was', 'a', 

...

['<bos>', 'nbc', 'broadcast', 'throughout', 'the', 'entire', 'night', 'and', 'did', 'not', 'go', 'off', 'the', 'air', 'until', 'noon', 'yesterday', '<eos>']
['<bos>', 'the', 'quake', 'postponed', 'the', 'third', 'and', 'fourth', 'games', 'of', 'the', 'world', 'series', '<eos>']
['<bos>', 'in', 'place', 'of', 'the', 'games', 'abc', 'said', 'it', 'planned', 'to', 'broadcast', 'next', 'week', "'s", 'episodes', 'of', 'its', 'prime-time', 'wednesday', 'and', 'thursday', '<unk>', 'except', 'for', 'a', 'one-hour', 'special', 'on', 'the', 'earthquake', 'at', 'N', 'p.m.', 'last', 'night', '<eos>']
['<bos>', 'the', 'series', 'is', 'scheduled', 'to', 'resume', 'tuesday', 'evening', 'in', 'san', 'francisco', '<eos>']
['<bos>', 'there', 'are', 'no', 'commercials', 'to', 'make', 'up', 'for', 'since', 'we', "'re", 'going', 'to', 'eventually', 'broadcast', 'the', 'world', 'series', 'said', 'a', 'network', 'spokesman', '<eos>']
['<bos>', 'pinnacle', 'west', 'capital', 'corp.', 'said', 'it', 'suspended'

['<bos>', 'in', 'texas', 'after', 'hurricane', '<unk>', 'major', 'grocery', 'chains', 'used', 'their', 'truck', 'fleets', 'to', 'ship', 'essential', 'goods', 'to', 'houston', 'no', '<unk>', 'just', 'good', 'will', '<eos>']
['<bos>', 'tom', '<unk>', '<eos>']
['<bos>', '<unk>', 'texas', '<eos>']
['<bos>', 'we', 'here', 'in', 'the', 'affected', 'areas', 'were', '<unk>', 'by', 'mr.', 'laband', "'s", 'analysis', 'of', 'time', 'values', 'and', 'his', 'comparisons', 'of', 'effectiveness', 'concerning', 'research', 'and', 'development', '<eos>']
['<bos>', 'his', 'theoretical', 'approach', 'and', 'its', 'publication', 'in', 'this', 'venerable', 'paper', 'are', 'no', 'doubt', 'a', '<unk>', '<unk>', 'for', 'him', '<eos>']
['<bos>', 'too', 'bad', 'theory', 'fails', 'in', 'practice', '<eos>']
['<bos>', 'we', 'consumers', 'tend', 'to', 'have', 'long', 'memories', '<eos>']
['<bos>', 'the', 'businesses', '<unk>', 'to', 'mr.', 'laband', "'s", 'effective', 'price', 'system', 'will', 'be', 'remembered', 

['<bos>', 'experts', 'on', 'sales', 'technique', 'say', 'anyone', 'representing', 'a', 'troubled', 'company', 'must', 'walk', 'a', 'fine', 'line', '<eos>']
['<bos>', 'if', 'a', 'salesman', '<unk>', 'his', 'credibility', 'in', 'this', 'time', 'of', 'trouble', 'it', 'will', 'be', 'a', 'problem', 'for', 'the', 'long', 'run', 'says', 'george', '<unk>', 'a', '<unk>', 'nev.', 'sales', 'consultant', 'and', 'author', 'of', 'the', 'marketing', 'edge', '<eos>']
['<bos>', 'still', 'says', 'john', 'sullivan', 'a', 'management', '<unk>', 'with', 'daniel', 'roberts', 'inc.', 'of', 'boston', 'who', 'has', 'held', 'senior', 'sales', 'positions', 'at', 'polaroid', 'and', '<unk>', 'the', 'customer', 'will', 'react', 'to', 'strength', '<eos>']
['<bos>', 'ignore', 'the', 'present', 'condition', '<eos>']
['<bos>', 'show', 'it', "'s", 'business', 'as', 'usual', '<eos>']
['<bos>', 'that', 'is', "n't", 'easy', '<eos>']
['<bos>', 'wang', "'s", 'customers', 'are', 'data', 'processing', 'managers', 'who', 'want'

['<bos>', 'the', 'contract', 'was', 'negotiated', 'by', 'the', 'countries', "'", 'two', 'prime', 'ministers', 'and', 'was', 'supposed', 'to', 'be', 'free', 'of', 'commissions', 'or', 'agents', "'", 'costs', '<eos>']
['<bos>', 'in', 'april', 'N', 'evidence', 'surfaced', 'that', 'commissions', 'were', 'paid', '<eos>']
['<bos>', 'the', 'opposition', 'charged', 'that', 'the', 'money', 'was', 'used', 'to', 'bribe', 'indian', 'government', 'officials', 'an', '<unk>', 'denied', 'by', 'mr.', 'gandhi', "'s", 'administration', '<eos>']
['<bos>', 'but', 'many', 'of', 'his', 'statements', 'on', 'the', 'issue', 'in', 'parliament', 'subsequently', 'were', 'proven', 'wrong', 'by', '<unk>', 'evidence', '<eos>']
['<bos>', 'the', 'scandal', 'has', 'faded', 'and', '<unk>', 'but', 'recent', 'disclosures', 'propelled', 'it', 'back', 'onto', 'the', 'front', 'pages', 'and', 'that', 'has', 'helped', '<unk>', 'the', 'opposition', 'which', 'last', 'week', 'blocked', 'passage', 'of', 'two', 'constitutional', 'am

['<bos>', 'there', "'s", 'quite', 'a', 'bit', 'of', 'value', 'left', 'in', 'the', 'jaguar', 'shares', 'here', 'even', 'though', 'they', 'have', 'run', 'up', 'lately', 'says', 'doug', 'johnson', 'a', 'fund', 'manager', 'for', '<unk>', '<unk>', 'asset', 'management', '<eos>']
['<bos>', 'at', 'the', 'moment', 'he', 'intends', 'to', 'keep', 'the', 'firm', "'s", 'N', 'jaguar', 'shares', '<eos>']
['<bos>', 'the', 'risk', 'is', 'that', 'jaguar', "'s", 'share', 'price', 'could', 'slump', 'if', 'gm', "'s", 'agreement', 'with', 'jaguar', 'effectively', '<unk>', 'out', 'its', 'u.s.', 'rival', '<eos>']
['<bos>', 'ford', "'s", 'appetite', 'to', 'attack', 'jaguar', 'could', 'gradually', '<unk>', 'over', 'time', 'particularly', 'if', 'saab', 'is', 'a', 'reasonably', 'attractive', 'proposition', 'says', 'john', 'lawson', 'an', 'auto', 'analyst', 'at', 'london', "'s", 'nomura', 'research', 'institute', '<eos>']
['<bos>', 'he', 'thinks', 'saab-scania', 'ab', 'on', 'friday', 'will', 'announce', 'the', 's

In [ ]:
def compute_prob0(sentence, dictionary_prob):
    prob = 1
    for word in sentence.split():
        if word in dictionary:
            prob = prob*dictionary_prob[word]
        else:
            prob = prob * dictionary_prob['<unk>']
    return prob

If you completed the task correctly then your function should compute:

p("my name is madina") = 8.512130344833542e-10

p("hello how are you") = 6.89010961921847e-13

p("this is an estimate") = 4.418442586905126e-10

In [13]:
p("my" | "\<bos>") * p("name" | "my") * p("is" | "name") * p("\<unk>" | "is") * p("\<eos>" | "\<unk>")

NameError: name 'p' is not defined

### Task 2: Predicting the most likely next words (Autocomplete)
In this task, you will implement autocomplete function which is similar to the message completion service in mobile phones.

Write a function **autofill** which takes a word and integer k as input (and maybe some additional arguments) and returns k most probable words to follow it according to the estimates computed by first order Markov chain.


If you completed the task correctly, your function should return that the 5 most probable words to follow "san" are \['francisco', '\<unk>', 'jose', 'diego', 'antonio'\]

### Task 3: Generate a text (zeroth order Markov chain)
Write a function **generate_text0** which takes as an input integer k (and maybe some additional arguments) and generates k sentences sampled from the probability distribution estimated by the zeroth order Markov chain. 

The length of each sentence should be at least 3 words, including \<bos> and \<eos>. For example "\<bos> is \<eos>".

\<bos> and \<eos> must not appear in the middle of a sentence.

Hint: you can use random.choices() for sampling.

If you completed the task correctly, then for k = 2 your output would look like this (but with different sentences):

['\<bos> fees property the year 's drop world died or \<unk> j. trust the which for meanwhile action economic criminal germany \<unk> by with white \<eos>',

 '\<bos> koch to a N laws \<eos>']

### Task 4: Generate a text (first order Markov chain)
Write a function **generate_text1** which takes as an input integer k (and maybe some additional arguments) and generates k sentences sampled from the probability distribution estimated using the first order Markov chain.

The length of each sentence should be at least 3 words, including \<bos> and \<eos>. For example "\<bos> is \<eos>".

\<bos> and \<eos> must not appear in the middle of a sentence.

Hint: you can use random.choices() for sampling.

If you completed the task correctly, then for k = 2 your output would look like this (but with different sentences):

['\<bos> what happened at st. louis assembly business \<eos>',

 '\<bos> integrated combines some people familiar with forecasts \<eos>',